In [2]:
import pandas as pd
from datetime import datetime

from components.freelancer import _get_project_by_id, _search_projects
from components.proposal import generate_proposal

def create_df(query, limit):
    p = _search_projects(query, limit)

    # Assuming 'p' is your JSON data
    data = p['projects']

    # Flatten the data
    df = pd.json_normalize(data)

    # Convert column names with '.' to '_'
    df.columns = df.columns.str.replace('.', '_')

    # Define the columns you want to keep
    columns = ['id', 'title', 'seo_url', 'submitdate', 'budget_minimum', 'budget_maximum', 'currency_code', 'currency_exchange_rate', 'bid_stats_bid_count', 'bid_stats_bid_avg']

    # Create a new DataFrame with only the columns you want
    df_filtered = df[columns]

    # Convert the budget columns to USD
    df_filtered['budget_maximum_usd'] = df_filtered['budget_maximum'] * df_filtered['currency_exchange_rate']
    df_filtered['budget_minimum_usd'] = df_filtered['budget_minimum'] * df_filtered['currency_exchange_rate']

    # Define your function
    def get_description(id):
        # Replace this with your actual function
        return _get_project_by_id(id)['description']

    # Create a new column 'description' by applying 'get_description' to each ID
    df_filtered['description'] = df_filtered['id'].apply(get_description)

    # Convert the 'submitdate' to a human-readable format
    df_filtered['submitdate'] = df_filtered['submitdate'].apply(lambda x: datetime.utcfromtimestamp(x).strftime('%Y-%m-%d %H:%M:%S'))

    # Convert the 'submitdate' to a datetime object
    df_filtered['submitdate'] = pd.to_datetime(df_filtered['submitdate'])

    # Generate proposals
    df_filtered['proposal'] = df_filtered.apply(lambda row: generate_proposal(row['title'], row['description']), axis=1)

    print("DataFrame name: df_filtered")  # Print the name of the DataFrame
   


ModuleNotFoundError: No module named 'components'

In [6]:
p

{'projects': [{'id': 37857786,
   'owner_id': 74877488,
   'title': 'Modern Logo Design for Global Company -- 2',
   'status': 'active',
   'sub_status': None,
   'seo_url': 'graphic-design/Modern-Logo-Design-for-Global-37857786',
   'currency': {'id': 11,
    'code': 'INR',
    'sign': '₹',
    'name': 'Indian Rupee',
    'exchange_rate': 0.012084,
    'country': 'IN',
    'is_external': False,
    'is_escrowcom_supported': False},
   'description': None,
   'jobs': None,
   'submitdate': 1709969539,
   'preview_description': "I'm looking for an aesthetic genius to create a unique, modern logo for a global company. Here's wha",
   'deleted': False,
   'nonpublic': False,
   'hidebids': False,
   'type': 'hourly',
   'bidperiod': 7,
   'budget': {'minimum': 750.0,
    'maximum': 1250.0,
    'name': None,
    'project_type': None,
    'currency_id': None},
   'hourly_project_info': {'commitment': {'hours': 40, 'interval': 'week'},
    'duration_enum': 'unspecified'},
   'featured': Fals

In [7]:
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import get_jobs
from freelancersdk.resources.projects.exceptions import \
    JobsNotFoundException
import os


def sample_get_jobs():
    url = os.environ.get('FLN_URL')
    oauth_token = ("cNwg3jpAAfrYOCXNiZJ4IBIWXvS57W")
    session = Session(oauth_token=oauth_token, url=url)

    get_jobs_data = {
        'job_ids': [
            20,
            32,
        ],
        'seo_details': True,
        'lang': 'en',
    }

    try:
        j = get_jobs(session, **get_jobs_data)
    except JobsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return j


j = sample_get_jobs()
if j:
    print('Found jobs: {}'.format(len(j)))

Found jobs: 2


In [8]:
j

[{'id': 20,
  'name': 'Graphic Design',
  'category': {'id': 3, 'name': 'Design, Media & Architecture'},
  'active_project_count': None,
  'seo_url': 'graphic_design',
  'seo_info': {'seo_text': '<p>Frequently a company is critiqued based on its visual presence, often in advance of any business interaction. Hiring the<em> bes</em><em>t</em>\xa0graphic designers plays a pivotal role in engendering respect and driving key business outcomes as they conceptualize and produce artwork or designs to enhance the transfer of visual messages and information.\xa0\xa0</p><p>The application of <a href="../../what-is-graphic-design-about">graphic design</a> is extensive and can encompass the following areas:</p><ul><li>Simple logos or various different types of logos;</li><li>Publications both printed and digitalized;</li><li>Promotional advertising such as posters, billboards or digital banners;</li><li>Creating entire website design, the best homepage designs\xa0or individual graphical elements;</

In [9]:
from freelancersdk.session import Session
from freelancersdk.resources.users.users import search_freelancers
from freelancersdk.resources.users.exceptions import UsersNotFoundException
from freelancersdk.resources.users.helpers import create_get_users_details_object
import os

def sample_search_freelancers():
    url = os.environ.get('FLN_URL')
    oauth_token = "cNwg3jpAAfrYOCXNiZJ4IBIWXvS57W"
    session = Session(oauth_token=oauth_token, url=url)
    user_details = create_get_users_details_object(
        cover_image=True,
        reputation=True,
        display_info=True
    )
    try:
        result = search_freelancers(
            session,
            query='design',
            user_details=user_details,
        )
    except UsersNotFoundException as e:
        print('Error message:', e)  # Print the exception object directly
        print('Server response:', e.error_code)
        return None
    else:
        return result

result = sample_search_freelancers()

if result:
    print('Found freelancers:', result)


Error message: Cannot request multiple users cover images
Server response: UserExceptionCodes.INVALID_REQUEST


In [10]:
result = sample_search_freelancers()


Error message: Cannot request multiple users cover images
Server response: UserExceptionCodes.INVALID_REQUEST


In [11]:
from freelancersdk.resources.projects import highlight_project_bid
from freelancersdk.session import Session
from freelancersdk.exceptions import BidNotHighlightedException
import os

def sample_highlight_project_bid():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    bid_id = os.environ.get('BID_ID')

    session = Session(oauth_token=oauth_token, url=url)

    try:
        return highlight_project_bid(session, bid_id)
    except BidNotHighlightedException as e:
        print('Error highlighting bid:', e.error_code)
        return None

b = sample_highlight_project_bid()
if b:
    print("Bid highlighted:", b)


Error highlighting bid: RestExceptionCodes.GENERAL


In [2]:
from freelancersdk.resources.projects import place_project_bid
from freelancersdk.session import Session
from freelancersdk.resources.users import get_self_user_id
from freelancersdk.exceptions import BidNotPlacedException
import os

# https://www.freelancer.com/api/docs/cases/creating_a_bid
def sample_place_project_bid():
    url = os.environ.get('FLN_URL')
    oauth_token ="cNwg3jpAAfrYOCXNiZJ4IBIWXvS57W"
    project_id = os.environ.get('PROJECT_ID')

    session = Session(oauth_token=oauth_token, url=url)

    try:
        my_user_id = get_self_user_id(session)
    except:
        # User ID not retrieved. Handle the error here, e.g., print an error message.
        return None

    bid_data = {
        'project_id': int(project_id),
        'bidder_id': my_user_id,
        'amount': 10,
        'period': 2,
        'milestone_percentage': 100,
        'description': 'This is my bid',
    }

    try:
        return place_project_bid(session, **bid_data)
    except BidNotPlacedException as e:
        print(('Error message: %s' % e.message))
        print(('Error code: %s' % e.error_code))
        return None


b = sample_place_project_bid()
if b:
    print(("Bid placed: %s" % b))

In [13]:
b

In [14]:
from freelancersdk.session import Session
from freelancersdk.resources.projects import retract_project_bid
from freelancersdk.exceptions import BidNotRetractedException
import os

# https://developers.freelancer.com/docs/use-cases/performing-a-bid-action
def sample_retract_project_bid():
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    url = os.environ.get('FLN_URL')
    session = Session(oauth_token=oauth_token, url=url)

    bid_data = {
        'bid_id': 1
    }

    try:
        return retract_project_bid(session, **bid_data)
    except BidNotRetractedException as e:
        print('Error message:', str(e))  # Accessing error message using str(e)
        print(('Error code: %s' % e.error_code))
        return None

b = sample_retract_project_bid()
if b:
    print(("Bid retracted: %s" % b))


Error message: You must be logged in to perform this request
Error code: RestExceptionCodes.NOT_AUTHENTICATED


In [15]:
from freelancersdk.session import Session
from freelancersdk.resources.projects import (
    search_projects, 
    highlight_project_bid, 
    place_project_bid, 
    retract_project_bid,
    revoke_project_bid,
)
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.exceptions import (
    BidNotPlacedException, 
    BidNotHighlightedException, 
    BidNotRetractedException,
    BidNotRevokedException,
)
import os

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = 'Logo Design'
    search_filter = {
        'sort_field': 'time_updated',
        'or_search_query': True
    }

    try:
        p = search_projects(session, query=query, search_filter=search_filter)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_highlight_project_bid():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    bid_id = os.environ.get('BID_ID')
    session = Session(oauth_token=oauth_token, url=url)

    try:
        return highlight_project_bid(session, bid_id)
    except BidNotHighlightedException as e:
        print('Error highlighting bid:', e.error_code)
        return None

def sample_place_project_bid():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')
    session = Session(oauth_token=oauth_token, url=url)

    try:
        my_user_id = get_self_user_id(session)
    except:
        # User ID not retrieved. Handle the error here, e.g., print an error message.
        return None

    bid_data = {
        'project_id': int(project_id),
        'bidder_id': my_user_id,
        'amount': 10,
        'period': 2,
        'milestone_percentage': 100,
        'description': 'This is my bid',
    }

    try:
        return place_project_bid(session, **bid_data)
    except BidNotPlacedException as e:
        print(('Error message: %s' % e.message))
        print(('Error code: %s' % e.error_code))
        return None

def sample_retract_project_bid():
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    url = os.environ.get('FLN_URL')
    session = Session(oauth_token=oauth_token, url=url)

    bid_data = {
        'bid_id': 1
    }

    try:
        return retract_project_bid(session, **bid_data)
    except BidNotRetractedException as e:
        print('Error message:', str(e))  # Accessing error message using str(e)
        print(('Error code: %s' % e.error_code))
        return None

def sample_revoke_project_bid():
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    url = os.environ.get('FLN_URL')
    session = Session(oauth_token=oauth_token, url=url)

    bid_data = {
        'bid_id': 1
    }

    try:
        return revoke_project_bid(session, **bid_data)
    except BidNotRevokedException as e:
        print(('Error message: %s' % e))
        return None

# Main code execution
if __name__ == "__main__":
    p = sample_search_projects()
    if p:
        print('Found projects: {}'.format(p))

    b = sample_highlight_project_bid()
    if b:
        print("Bid highlighted:", b)

    b = sample_place_project_bid()
    if b:
        print(("Bid placed: %s" % b))

    b = sample_retract_project_bid()
    if b:
        print(("Bid retracted: %s" % b))

    b = sample_revoke_project_bid()
    if b:
        print(("Bid revoked: %s" % b))


Found projects: {'projects': [{'id': 37857786, 'owner_id': 74877488, 'title': 'Modern Logo Design for Global Company -- 2', 'status': 'active', 'sub_status': None, 'seo_url': 'graphic-design/Modern-Logo-Design-for-Global-37857786', 'currency': {'id': 11, 'code': 'INR', 'sign': '₹', 'name': 'Indian Rupee', 'exchange_rate': 0.012084, 'country': 'IN', 'is_external': False, 'is_escrowcom_supported': False}, 'description': None, 'jobs': None, 'submitdate': 1709969539, 'preview_description': "I'm looking for an aesthetic genius to create a unique, modern logo for a global company. Here's wha", 'deleted': False, 'nonpublic': False, 'hidebids': False, 'type': 'hourly', 'bidperiod': 7, 'budget': {'minimum': 750.0, 'maximum': 1250.0, 'name': None, 'project_type': None, 'currency_id': None}, 'hourly_project_info': {'commitment': {'hours': 40, 'interval': 'week'}, 'duration_enum': 'unspecified'}, 'featured': False, 'urgent': False, 'assisted': None, 'active_prepaid_milestone': None, 'bid_stats': {

In [16]:
from freelancersdk.resources.projects import create_milestone_payment
from freelancersdk.resources.projects.types import MilestoneReason
from freelancersdk.session import Session
from freelancersdk.exceptions import MilestoneNotCreatedException
import os


# https://www.freelancer.com/api/docs/cases/creating_a_milestone
def sample_create_milestone_payment():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')
    bidder_id = os.environ.get('BIDDER_ID')

    if not all([url, oauth_token, project_id, bidder_id]):
        print("Missing required environment variables.")
        return None

    try:
        project_id = int(project_id)
        bidder_id = int(bidder_id)
    except (TypeError, ValueError):
        print("Invalid project_id or bidder_id.")
        return None

    session = Session(oauth_token=oauth_token, url=url)
    milestone_data = {
        'project_id': project_id,
        'bidder_id': bidder_id,
        'amount': 10,
        'reason': MilestoneReason.PARTIAL_PAYMENT.value,
        'description': 'This is a milestone',
    }

    try:
        m = create_milestone_payment(session, **milestone_data)
    except MilestoneNotCreatedException as e:
        print(('Error message: %s' % e.message))
        print(('Server response: %s' % e.error_code))
        return None
    else:
        return m

m = sample_create_milestone_payment()
if m:
    print(("Milestone created: %s" % m))


Missing required environment variables.


In [17]:
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    get_projects, get_project_by_id
)
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.projects.exceptions import \
    ProjectsNotFoundException
import os
import json


def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = create_get_projects_object(
        project_ids=[
            201,
            202,
            203,
        ],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p


print('Getting multiple projects...')
p = sample_get_projects()
if p:
    print('Found projects: {}'.format(json.dumps(p)))
print('Getting a single project by ID...')

p = sample_get_project_by_id()
if p:
    print('Found a single project: {}'.format(json.dumps(p)))



Getting multiple projects...
Found projects: {"projects": [{"id": 201, "owner_id": 2684, "title": "Boot to application", "status": "closed", "sub_status": "closed_expired", "seo_url": "Boot-application-project", "currency": {"id": 1, "code": "USD", "sign": "$", "name": "US Dollar", "exchange_rate": 1.0, "country": "US", "is_external": false, "is_escrowcom_supported": true}, "description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the computer loads an application and displays files on the monitor without any further interaction after switching on. i.e no passwords, start menu-application, etc.  I envisage boot - load browser - display html files (starting with home page) It could be some other application, but browser/html files seems the most common and, because these files have to be uploaded would probably be easier. ", "jobs": [], "submitdate": 1077810438, "preview_description": "To provide a boot sequence for ms windows such that from swit

In [18]:
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    get_projects, get_project_by_id
)
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.projects.exceptions import \
    ProjectsNotFoundException
import os
import json


def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = create_get_projects_object(
        project_ids=[
            201,
            202,
            203,
        ],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p


print('Getting multiple projects...')
p = sample_get_projects()
if p:
    print('Found projects: {}'.format(json.dumps(p)))
print('Getting a single project by ID...')

p = sample_get_project_by_id()
if p:
    print('Found a single project: {}'.format(json.dumps(p)))



Getting multiple projects...
Found projects: {"projects": [{"id": 201, "owner_id": 2684, "title": "Boot to application", "status": "closed", "sub_status": "closed_expired", "seo_url": "Boot-application-project", "currency": {"id": 1, "code": "USD", "sign": "$", "name": "US Dollar", "exchange_rate": 1.0, "country": "US", "is_external": false, "is_escrowcom_supported": true}, "description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the computer loads an application and displays files on the monitor without any further interaction after switching on. i.e no passwords, start menu-application, etc.  I envisage boot - load browser - display html files (starting with home page) It could be some other application, but browser/html files seems the most common and, because these files have to be uploaded would probably be easier. ", "jobs": [], "submitdate": 1077810438, "preview_description": "To provide a boot sequence for ms windows such that from swit

In [19]:
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    search_projects, get_projects, get_project_by_id, place_project_bid,
    create_milestone_payment
)
from freelancersdk.resources.projects.exceptions import (
    ProjectsNotFoundException, BidNotPlacedException, MilestoneNotCreatedException
)
from freelancersdk.resources.projects.helpers import (
    create_search_projects_filter, create_get_projects_object,
    create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.projects.types import MilestoneReason
import os
import json

# Function to search for projects
def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    search_filter = create_search_projects_filter(
        sort_field='time_updated',
        or_search_query=True,
    )

    try:
        p = search_projects(session, query=query, search_filter=search_filter)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

# Function to retrieve details of multiple projects
def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = create_get_projects_object(
        project_ids=[201, 202, 203],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

# Function to retrieve details of a single project by ID
def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

# Function to create a bid for a project
def sample_create_project_bid():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')

    if not all([url, oauth_token, project_id]):
        print("Missing required environment variables.")
        return None

    session = Session(oauth_token=oauth_token)

    bid_data = {
        'project_id': int(project_id),
        'amount': 10,
        'period': 2,
        'milestone_percentage': 100,
        'description': 'This is my bid',
    }

    try:
        return place_project_bid(session, **bid_data)
    except BidNotPlacedException as e:
        print(('Error message: %s' % e.message))
        print(('Error code: %s' % e.error_code))
        return None

# Function to create a milestone payment for a project
def sample_create_milestone_payment():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')
    bidder_id = os.environ.get('BIDDER_ID')

    if not all([url, oauth_token, project_id, bidder_id]):
        print("Missing required environment variables.")
        return None

    try:
        project_id = int(project_id)
        bidder_id = int(bidder_id)
    except (TypeError, ValueError):
        print("Invalid project_id or bidder_id.")
        return None

    session = Session(oauth_token=oauth_token)
    milestone_data = {
        'project_id': project_id,
        'bidder_id': bidder_id,
        'amount': 10,
        'reason': MilestoneReason.PARTIAL_PAYMENT.value,
        'description': 'This is a milestone',
    }

    try:
        m = create_milestone_payment(session, **milestone_data)
    except MilestoneNotCreatedException as e:
        print(('Error message: %s' % e.message))
        print(('Server response: %s' % e.error_code))
        return None
    else:
        return m

# Main program
if __name__ == "__main__":
    print('Searching for projects...')
    projects = sample_search_projects()
    if projects:
        print('Found projects: {}'.format(json.dumps(projects)))

    print('Retrieving details of multiple projects...')
    multiple_projects = sample_get_projects()
    if multiple_projects:
        print('Details of multiple projects: {}'.format(json.dumps(multiple_projects)))

    print('Retrieving details of a single project by ID...')
    single_project = sample_get_project_by_id()
    if single_project:
        print('Details of a single project: {}'.format(json.dumps(single_project)))

    print('Creating a bid for a project...')
    bid_created = sample_create_project_bid()
    if bid_created:
        print('Bid created: {}'.format(bid_created))

    print('Creating a milestone payment...')
    milestone_created = sample_create_milestone_payment()
    if milestone_created:
        print('Milestone created: {}'.format(milestone_created))


Searching for projects...
Found projects: {"projects": [{"id": 37857786, "owner_id": 74877488, "title": "Modern Logo Design for Global Company -- 2", "status": "active", "sub_status": null, "seo_url": "graphic-design/Modern-Logo-Design-for-Global-37857786", "currency": {"id": 11, "code": "INR", "sign": "\u20b9", "name": "Indian Rupee", "exchange_rate": 0.012084, "country": "IN", "is_external": false, "is_escrowcom_supported": false}, "description": null, "jobs": null, "submitdate": 1709969539, "preview_description": "I'm looking for an aesthetic genius to create a unique, modern logo for a global company. Here's wha", "deleted": false, "nonpublic": false, "hidebids": false, "type": "hourly", "bidperiod": 7, "budget": {"minimum": 750.0, "maximum": 1250.0, "name": null, "project_type": null, "currency_id": null}, "hourly_project_info": {"commitment": {"hours": 40, "interval": "week"}, "duration_enum": "unspecified"}, "featured": false, "urgent": false, "assisted": null, "active_prepaid_m

In [20]:
import pandas as pd

# Create a DataFrame with colors
colors_df = pd.DataFrame(data=[['red'],['blue'],['green'],['blue']], columns=['color'])

# Print the DataFrame before One Hot Encoding
print('Before One Hot Encoding:')
print(colors_df)

# Perform one-hot encoding using pandas get_dummies() function
colors_df_encoded = pd.get_dummies(colors_df)

# Print the encoded colors
print('After One Hot Encoding:')
print(colors_df_encoded)


Before One Hot Encoding:
   color
0    red
1   blue
2  green
3   blue
After One Hot Encoding:
   color_blue  color_green  color_red
0       False        False       True
1        True        False      False
2       False         True      False
3        True        False      False


In [21]:
import pandas as pd
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects.helpers import (
    create_search_projects_filter,
    create_get_projects_user_details_object,
    create_get_projects_project_details_object,
)
import os

def sample_search_projects_to_csv():
    url = os.environ.get('FLN_URL')
    oauth_token = 'cNwg3jpAAfrYOCXNiZJ4IBIWXvS57W'
    session = Session(oauth_token=oauth_token, url=url)

    query = 'Logo Design'
    search_filter = create_search_projects_filter(
        sort_field='time_updated',
        or_search_query=True,
    )

    try:
        projects = search_projects(session, query=query, search_filter=search_filter)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return

    # Create a DataFrame from the search results
    projects_df = pd.DataFrame(projects)

    # Specify the path to save the CSV file
    csv_file_path = 'projects_search_results.csv'

    # Save the DataFrame to a CSV file
    projects_df.to_csv(csv_file_path, index=False)

    print('Search results saved to:', csv_file_path)

sample_search_projects_to_csv()


Search results saved to: projects_search_results.csv


In [22]:
import pandas as pd
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects.helpers import (
    create_search_projects_filter,
    create_get_projects_user_details_object,
    create_get_projects_project_details_object,
)
import os

def sample_search_projects_to_csv():
    url = os.environ.get('FLN_URL')
    oauth_token = 'cNwg3jpAAfrYOCXNiZJ4IBIWXvS57W'
    session = Session(oauth_token=oauth_token, url=url)

    query = 'Logo Design'
    search_filter = create_search_projects_filter(
        sort_field='time_updated',
        or_search_query=True,
    )

    try:
        projects = search_projects(session, query=query, search_filter=search_filter)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return

    # Create a DataFrame from the search results
    projects_df = pd.DataFrame(projects)

    # Display the DataFrame in a user-friendly format
    for index, row in projects_df.iterrows():
        print(f"Project {index + 1}:")
        for column, value in row.items():
            print(f"{column}: {value}")
        print()

    # Specify the path to save the CSV file
    csv_file_path = 'projects_search_results.csv'

    # Save the DataFrame to a CSV file
    projects_df.to_csv(csv_file_path, index=False)

    print('Search results saved to:', csv_file_path)

sample_search_projects_to_csv()

Project 1:
projects: {'id': 37857786, 'owner_id': 74877488, 'title': 'Modern Logo Design for Global Company -- 2', 'status': 'active', 'sub_status': None, 'seo_url': 'graphic-design/Modern-Logo-Design-for-Global-37857786', 'currency': {'id': 11, 'code': 'INR', 'sign': '₹', 'name': 'Indian Rupee', 'exchange_rate': 0.012084, 'country': 'IN', 'is_external': False, 'is_escrowcom_supported': False}, 'description': None, 'jobs': None, 'submitdate': 1709969539, 'preview_description': "I'm looking for an aesthetic genius to create a unique, modern logo for a global company. Here's wha", 'deleted': False, 'nonpublic': False, 'hidebids': False, 'type': 'hourly', 'bidperiod': 7, 'budget': {'minimum': 750.0, 'maximum': 1250.0, 'name': None, 'project_type': None, 'currency_id': None}, 'hourly_project_info': {'commitment': {'hours': 40, 'interval': 'week'}, 'duration_enum': 'unspecified'}, 'featured': False, 'urgent': False, 'assisted': None, 'active_prepaid_milestone': None, 'bid_stats': {'bid_coun

In [23]:
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects.helpers import create_search_projects_filter
from tabulate import tabulate
import os
from dotenv import load_dotenv

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    search_filter = create_search_projects_filter(
        sort_field='time_updated',
        or_search_query=True,
    )

    try:
        response = search_projects(
            session,
            query=query,
            search_filter=search_filter
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    headers = [
        "Project ID", "Owner ID", "Title", "Description", "Budget",
        "Currency Type", "Currency Symbol", "Date Updated", "Status",
        "Deleted", "Nonpublic", "Hide Bids", "Type", "Bid Period",
        "Featured", "Urgent", "Assisted", "Active Prepaid Milestone",
        "Bid Stats: Bid Count", "Bid Stats: Bid Avg",
        "Upgrades: Featured", "Upgrades: Sealed", "Upgrades: Nonpublic",
        "Upgrades: Fulltime", "Upgrades: Urgent", "Upgrades: Qualified",
        "Upgrades: NDA", "Upgrades: Assisted", "Upgrades: Active Prepaid Milestone",
        "Upgrades: IP Contract", "Upgrades: Success Bundle", "Upgrades: Non Compete",
        "Upgrades: Project Management", "Upgrades: PF Only", "Upgrades: Recruiter",
        "Upgrades: Listed", "Upgrades: Extend", "Upgrades: Unpaid Recruiter",
        "Upgrades: Premium", "Upgrades: Enterprise",
        "Qualifications", "Language", "Attachments", "Hireme", "Hireme Initial Bid",
        "Invited Freelancers", "Recommended Freelancers", "Frontend Project Status",
        "NDA Signatures",
        "Location: Country: Name", "Location: Country: Flag URL", "Location: Country: Code",
        "Location: Country: Highres Flag URL", "Location: Country: Flag URL CDN",
        "Location: Country: Highres Flag URL CDN", "Location: Country: ISO3",
        "Location: Country: Region ID", "Location: Country: Phone Code",
        "Location: Country: Demonym", "Location: Country: Person",
        "Location: Country: SEO URL", "Location: Country: Sanction",
        "Location: Country: Language Code", "Location: Country: Language ID",
        "Upgrades: Time Free Bids Expire", "Files", "User Distance",
        "From User Location", "Project Collaborations", "Support Sessions",
        "Track IDs", "Drive Files", "NDA Details", "Pool IDs", "Enterprise IDs",
        "Timeframe", "Deloitte Details", "Is Escrow Project", "Is Seller KYC Required",
        "Is Buyer KYC Required", "Local Details", "Equipment", "NDA Signatures New",
        "Billing Code", "Enterprises", "Enterprise Metadata Values",
        "Project Reject Reason: Description", "Project Reject Reason: Message",
        "Repost ID", "Client Engagement", "Contract Signatures", "Quotation ID",
        "Quotation Version ID", "Enterprise Linked Projects Details", "Equipment Groups",
        "Quality Details", "Previous Recruiter Project Details", "Project Note",
        "Is Quotation Project", "Quotation Initial Bid", "Requires Upfront Funding",
        "Group IDs"
    ]
    # Extract project details into a list of lists
    project_data = []
    for project in projects:
        bid_stats = project.get("bid_stats", {})
        upgrades = project.get("upgrades", {})
        location = project.get("location", {})
        project_reject_reason = project.get("project_reject_reason", {})
        project_row = [
            project.get("id", ""),
            project.get("owner_id", ""),
            project.get("title", ""),
            project.get("description", ""),
            project.get("budget", {}).get("minimum", ""),
            project.get("currency", {}).get("name", ""),
            project.get("currency", {}).get("sign", ""),
            project.get("time_updated", ""),
            project.get("status", ""),
            project.get("deleted", ""),
            project.get("nonpublic", ""),
            project.get("hidebids", ""),
            project.get("type", ""),
            project.get("bidperiod", ""),
            upgrades.get("featured", ""),
            upgrades.get("urgent", ""),
            project.get("assisted", ""),
            project.get("active_prepaid_milestone", ""),
            bid_stats.get("bid_count", ""),
            bid_stats.get("bid_avg", ""),
            upgrades.get("featured", ""),
            upgrades.get("sealed", ""),
            upgrades.get("nonpublic", ""),
            upgrades.get("fulltime", ""),
            upgrades.get("urgent", ""),
            upgrades.get("qualified", ""),
            upgrades.get("nda", ""),
            upgrades.get("assisted", ""),
            upgrades.get("active_prepaid_milestone", ""),
            upgrades.get("ip_contract", ""),
            upgrades.get("success_bundle", ""),
            upgrades.get("non_compete", ""),
            upgrades.get("project_management", ""),
            upgrades.get("pf_only", ""),
            upgrades.get("recruiter", ""),
            upgrades.get("listed", ""),
            upgrades.get("extend", ""),
            upgrades.get("unpaid_recruiter", ""),
            upgrades.get("premium", ""),
            upgrades.get("enterprise", ""),
            project.get("qualifications", ""),
            project.get("language", ""),
            project.get("attachments", ""),
            project.get("hireme", ""),
            project.get("hireme_initial_bid", ""),
            project.get("invited_freelancers", ""),
            project.get("recommended_freelancers", ""),
            project.get("frontend_project_status", ""),
            project.get("nda_signatures", ""),
            location.get("country", {}).get("name", ""),
            location.get("country", {}).get("flag_url", ""),
            location.get("country", {}).get("code", ""),
            location.get("country", {}).get("highres_flag_url", ""),
            location.get("country", {}).get("flag_url_cdn", ""),
            location.get("country", {}).get("highres_flag_url_cdn", ""),
            location.get("country", {}).get("iso3", ""),
            location.get("country", {}).get("region_id", ""),
            location.get("country", {}).get("phone_code", ""),
            location.get("country", {}).get("demonym", ""),
            location.get("country", {}).get("person", ""),
            location.get("country", {}).get("seo_url", ""),
            location.get("country", {}).get("sanction", ""),
            location.get("country", {}).get("language_code", ""),
            location.get("country", {}).get("language_id", ""),
            upgrades.get("time_free_bids_expire", ""),
            project.get("files", ""),
            project.get("user_distance", ""),
            project.get("from_user_location", ""),
            project.get("project_collaborations", ""),
            project.get("support_sessions", ""),
            project.get("track_ids", ""),
            project.get("drive_files", ""),
            project.get("nda_details", ""),
            project.get("pool_ids", ""),
            project.get("enterprise_ids", ""),
            project.get("timeframe", ""),
            project.get("deloitte_details", ""),
            project.get("is_escrow_project", ""),
            project.get("is_seller_kyc_required", ""),
            project.get("is_buyer_kyc_required", ""),
            project.get("local_details", ""),
            project.get("equipment", ""),
            project.get("nda_signatures_new", ""),
            project.get("billing_code", ""),
            project.get("enterprises", ""),
            project.get("enterprise_metadata_values", ""),
            project_reject_reason.get("description", ""),
            project_reject_reason.get("message", ""),
            project.get("repost_id", ""),
            project.get("client_engagement", ""),
            project.get("contract_signatures", ""),
            project.get("quotation_id", ""),
            project.get("quotation_version_id", ""),
            project.get("enterprise_linked_projects_details", ""),
            project.get("equipment_groups", ""),
            project.get("quality_details", ""),
            project.get("previous_recruiter_project_details", ""),
            project.get("project_note", ""),
            project.get("is_quotation_project", ""),
            project.get("quotation_initial_bid", ""),
            project.get("requires_upfront_funding", ""),
            project.get("group_ids", "")
        ]
        project_data.append(project_row)

    # Print the table
    print(tabulate(project_data, headers=headers, tablefmt="grid"))

p = sample_search_projects()
print_projects_table(p)

+--------------+------------+-----------------------------------------------------+---------------+----------+-----------------+-------------------+----------------+----------+-----------+-------------+-------------+--------+--------------+------------+----------+------------+----------------------------+------------------------+----------------------+----------------------+--------------------+-----------------------+----------------------+--------------------+-----------------------+-----------------+----------------------+--------------------------------------+-------------------------+----------------------------+-------------------------+--------------------------------+---------------------+-----------------------+--------------------+--------------------+------------------------------+---------------------+------------------------+------------------+------------+---------------+----------+----------------------+-----------------------+---------------------------+----------------

In [24]:
import csv
import os
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects.helpers import create_search_projects_filter
from tabulate import tabulate

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    search_filter = create_search_projects_filter(
        sort_field='time_updated',
        or_search_query=True,
        
    )

    try:
        response = search_projects(
            session,
            query=query,
            search_filter=search_filter
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(projects[0].keys())  # Write header row
        for project in projects:
            writer.writerow(project.values())

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    headers = projects[0].keys()
    project_data = [project.values() for project in projects]

    # Print the table
    print(tabulate(project_data, headers=headers, tablefmt="grid"))

p = sample_search_projects()
save_projects_to_csv(p)
print_projects_table(p)


Search results saved to CSV file: projects_search_results.csv
+----------+------------+-----------------------------------------------------+----------+----------------+-------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+----------------------------------------------------------------------------------------------------+-----------------------------------------------------------------------------------+------------+----------+------------+----------------------------+--------------------------------------------------+------------------+----------------+--------------------------------------------------------------------

In [25]:
import csv
import os
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=10  # Set the limit to 50 directly in the search_projects call
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(projects[0].keys())  # Write header row
        for project in projects:
            writer.writerow(project.values())

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    headers = projects[0].keys()
    project_data = [project.values() for project in projects]

    # Print the table
    print(tabulate(project_data, headers=headers, tablefmt="grid"))

p = sample_search_projects()
save_projects_to_csv(p)
print_projects_table(p)


Search results saved to CSV file: projects_search_results.csv
+----------+------------+-----------------------------------------------------+----------+----------------+-------------------------------------------------------+-------------------------------------------------------------------------------------------------------------------------------------------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+----------------------------------------------------------------------------------------------------+-----------------------------------------------------------------------------------+------------+----------+------------+----------------------------+--------------------------------------------------+------------------+----------------+--------------------------------------------------------------------

In [26]:
import os
import csv
import json
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    get_projects, get_project_by_id, search_projects
)
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate

load_dotenv()

def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = create_get_projects_object(
        project_ids=[
            201,
            202,
            203,
        ],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=10  # Set the limit to 10 directly in the search_projects call
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(projects[0].keys())  # Write header row
        for project in projects:
            writer.writerow(project.values())

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    headers = projects[0].keys()
    project_data = [project.values() for project in projects]

    # Print the table
    print(tabulate(project_data, headers=headers, tablefmt="grid"))

print('Getting multiple projects...')
p = sample_get_projects()
if p:
    print('Found projects: {}'.format(json.dumps(p)))
print('Getting a single project by ID...')

p = sample_get_project_by_id()
if p:
    print('Found a single project: {}'.format(json.dumps(p)))

# Now let's perform a search for projects and save the results to a CSV file and print the results table.
searched_projects = sample_search_projects()
save_projects_to_csv(searched_projects)
print_projects_table(searched_projects)


Getting multiple projects...
Found projects: {"projects": [{"id": 201, "owner_id": 2684, "title": "Boot to application", "status": "closed", "sub_status": "closed_expired", "seo_url": "Boot-application-project", "currency": {"id": 1, "code": "USD", "sign": "$", "name": "US Dollar", "exchange_rate": 1.0, "country": "US", "is_external": false, "is_escrowcom_supported": true}, "description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the computer loads an application and displays files on the monitor without any further interaction after switching on. i.e no passwords, start menu-application, etc.  I envisage boot - load browser - display html files (starting with home page) It could be some other application, but browser/html files seems the most common and, because these files have to be uploaded would probably be easier. ", "jobs": [], "submitdate": 1077810438, "preview_description": "To provide a boot sequence for ms windows such that from swit

In [27]:
import os
import csv
import json
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    get_projects, get_project_by_id, search_projects, create_milestone_payment
)
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects.types import MilestoneReason
from tabulate import tabulate
from freelancersdk.exceptions import MilestoneNotCreatedException

load_dotenv()

def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = create_get_projects_object(
        project_ids=[
            201,
            202,
            203,
        ],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=10  # Set the limit to 10 directly in the search_projects call
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(projects[0].keys())  # Write header row
        for project in projects:
            writer.writerow(project.values())

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    headers = projects[0].keys()
    project_data = [project.values() for project in projects]

    # Print the table
    print(tabulate(project_data, headers=headers, tablefmt="grid"))

def sample_create_milestone_payment():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')
    bidder_id = os.environ.get('BIDDER_ID')

    if not all([url, oauth_token, project_id, bidder_id]):
        print("Missing required environment variables.")
        return None

    try:
        project_id = int(project_id)
        bidder_id = int(bidder_id)
    except (TypeError, ValueError):
        print("Invalid project_id or bidder_id.")
        return None

    session = Session(oauth_token=oauth_token, url=url)
    milestone_data = {
        'project_id': project_id,
        'bidder_id': bidder_id,
        'amount': 10,
        'reason': MilestoneReason.PARTIAL_PAYMENT.value,
        'description': 'This is a milestone',
    }

    try:
        m = create_milestone_payment(session, **milestone_data)
    except MilestoneNotCreatedException as e:
        print(('Error message: %s' % e.message))
        print(('Server response: %s' % e.error_code))
        return None
    else:
        return m

if __name__ == "__main__":
    print('Getting multiple projects...')
    p = sample_get_projects()
    if p:
        print('Found projects: {}'.format(json.dumps(p)))
    print('Getting a single project by ID...')
    p = sample_get_project_by_id()
    if p:
        print('Found a single project: {}'.format(json.dumps(p)))

    # Now let's perform a search for projects and save the results to a CSV file and print the results table.
    searched_projects = sample_search_projects()
    save_projects_to_csv(searched_projects)
    print_projects_table(searched_projects)

    # Creating a milestone payment
    m = sample_create_milestone_payment()
    if m:
        print(("Milestone created: %s" % m))


Getting multiple projects...


Found projects: {"projects": [{"id": 201, "owner_id": 2684, "title": "Boot to application", "status": "closed", "sub_status": "closed_expired", "seo_url": "Boot-application-project", "currency": {"id": 1, "code": "USD", "sign": "$", "name": "US Dollar", "exchange_rate": 1.0, "country": "US", "is_external": false, "is_escrowcom_supported": true}, "description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the computer loads an application and displays files on the monitor without any further interaction after switching on. i.e no passwords, start menu-application, etc.  I envisage boot - load browser - display html files (starting with home page) It could be some other application, but browser/html files seems the most common and, because these files have to be uploaded would probably be easier. ", "jobs": [], "submitdate": 1077810438, "preview_description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the com

In [28]:
import os
import csv
import json
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    get_projects, get_project_by_id, search_projects, create_milestone_payment, place_project_bid
)
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects.types import MilestoneReason
from tabulate import tabulate
from freelancersdk.exceptions import MilestoneNotCreatedException, BidNotPlacedException
from freelancersdk.resources.users import get_self_user_id

load_dotenv()

def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = create_get_projects_object(
        project_ids=[
            201,
            202,
            203,
        ],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=15  # Set the limit to 10 directly in the search_projects call
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(projects[0].keys())  # Write header row
        for project in projects:
            writer.writerow(project.values())

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    headers = projects[0].keys()
    project_data = [project.values() for project in projects]

    # Print the table
    print(tabulate(project_data, headers=headers, tablefmt="grid"))

def sample_create_milestone_payment():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')
    bidder_id = os.environ.get('BIDDER_ID')

    if not all([url, oauth_token, project_id, bidder_id]):
        print("Missing required environment variables.")
        return None

    try:
        project_id = int(project_id)
        bidder_id = int(bidder_id)
    except (TypeError, ValueError):
        print("Invalid project_id or bidder_id.")
        return None

    session = Session(oauth_token=oauth_token, url=url)
    milestone_data = {
        'project_id': project_id,
        'bidder_id': bidder_id,
        'amount': 10,
        'reason': MilestoneReason.PARTIAL_PAYMENT.value,
        'description': 'This is a milestone',
    }

    try:
        m = create_milestone_payment(session, **milestone_data)
    except MilestoneNotCreatedException as e:
        print(('Error message: %s' % e.message))
        print(('Server response: %s' % e.error_code))
        return None
    else:
        return m

def create_bid():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')

    session = Session(oauth_token=oauth_token, url=url)

    try:
        my_user_id = get_self_user_id(session)
    except:
        # User ID not retrieved. Handle the error here, e.g., print an error message.
        return None

    bid_data = {
        'project_id': int(project_id),
        'bidder_id': my_user_id,
        'amount': 10,
        'period': 2,
        'milestone_percentage': 100,
        'description': 'This is my bid',
    }

    try:
        return place_project_bid(session, **bid_data)
    except BidNotPlacedException as e:
        print(('Error message: %s' % e.message))
        print(('Error code: %s' % e.error_code))
        return None


if __name__ == "__main__":
    print('Getting multiple projects...')
    p = sample_get_projects()
    if p:
        print('Found projects: {}'.format(json.dumps(p)))
    print('Getting a single project by ID...')
    p = sample_get_project_by_id()
    if p:
        print('Found a single project: {}'.format(json.dumps(p)))

    # Now let's perform a search for projects and save the results to a CSV file and print the results table.
    searched_projects = sample_search_projects()
    save_projects_to_csv(searched_projects)
    print_projects_table(searched_projects)

    # Creating a milestone payment
    m = sample_create_milestone_payment()
    if m:
        print(("Milestone created: %s" % m))

    # Placing a project bid
    b = create_bid()
    if b:
        print(("Bid placed: %s" % b))


Getting multiple projects...
Found projects: {"projects": [{"id": 201, "owner_id": 2684, "title": "Boot to application", "status": "closed", "sub_status": "closed_expired", "seo_url": "Boot-application-project", "currency": {"id": 1, "code": "USD", "sign": "$", "name": "US Dollar", "exchange_rate": 1.0, "country": "US", "is_external": false, "is_escrowcom_supported": true}, "description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the computer loads an application and displays files on the monitor without any further interaction after switching on. i.e no passwords, start menu-application, etc.  I envisage boot - load browser - display html files (starting with home page) It could be some other application, but browser/html files seems the most common and, because these files have to be uploaded would probably be easier. ", "jobs": [], "submitdate": 1077810438, "preview_description": "To provide a boot sequence for ms windows such that from swit

In [29]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate
import json

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=100
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)

        # Write headers based on the structure of the projects
        header_row = []
        for key in projects[0].keys():
            if isinstance(projects[0][key], dict):
                for sub_key in projects[0][key].keys():
                    header_row.append(f"{key}_{sub_key}")
            else:
                header_row.append(key)
        writer.writerow(header_row)

        # Write project data
        for project in projects:
            data_row = []
            for key in project.keys():
                if isinstance(project[key], dict):
                    sub_data = project[key]
                    sub_data_list = [sub_data[sub_key] for sub_key in sub_data.keys()]
                    data_row.extend(sub_data_list)
                else:
                    data_row.append(project[key])
            writer.writerow(data_row)

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    # Extracting headers and project data
    headers = projects[0].keys()
    project_data = [list(project.values()) for project in projects]

    # Modifying headers to prefix each key with their respective categories
    modified_headers = []
    for header in headers:
        modified_headers.extend([f"{header}_{key}" for key in projects[0][header].keys()] if isinstance(projects[0][header], dict) else [header])

    # Modifying project data to include prefixed keys
    modified_project_data = []
    for project in project_data:
        modified_project = []
        for value in project:
            if isinstance(value, dict):
                modified_project.extend(value.values())
            else:
                modified_project.append(value)
        modified_project_data.append(modified_project)

    # Printing the table
    print(tabulate(modified_project_data, headers=modified_headers, tablefmt="grid")) 

p = sample_search_projects()
save_projects_to_csv(p)
print_projects_table(p)


Search results saved to CSV file: projects_search_results.csv
+----------+------------+-----------------------------------------------------------------------------+----------+----------------+-----------------------------------------------------------+---------------+-----------------+-----------------+-------------------+--------------------------+--------------------+------------------------+-----------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+------------------+------------------+---------------+-----------------------+----------------------+-----------------------------------+-------------------------------------+------------+----------+------------+----------------------------+-----------------------+---------------------+------------------+----------------+---------------------+----------------

In [30]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate

load_dotenv()

def extract_values(data, prefix=''):
    if isinstance(data, dict):
        result = []
        for key, value in data.items():
            result.extend(extract_values(value, prefix=f"{prefix}_{key}" if prefix else key))
        return result
    else:
        return [(prefix, data)]

def flatten_project_data(project):
    flattened_project = []
    for key, value in project.items():
        flattened_project.extend(extract_values(value, prefix=key))
    return flattened_project

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=30
        )

        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)

        modified_headers = []
        for key, _ in extract_values(projects[0]):
            modified_headers.append(key)

        writer.writerow(modified_headers)
        
        for project in projects:
            flattened_project = flatten_project_data(project)
            row_data = {key: value for key, value in flattened_project}
            writer.writerow([row_data.get(header, '') for header in modified_headers])

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    modified_headers = []
    for key, _ in extract_values(projects[0]):
        modified_headers.append(key)

    modified_project_data = [flatten_project_data(project) for project in projects]

    table_data = []
    for project_data in modified_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in modified_headers])

    print(tabulate(table_data, headers=modified_headers, tablefmt="grid"))

def print_hourly_project_info_table(projects):
    if not projects:
        print("No projects found.")
        return

    hourly_project_data = [flatten_project_data(project) for project in projects if project.get('projectType') == 'HOURLY']

    if not hourly_project_data:
        print("No hourly projects found.")
        return

    modified_headers = []
    for project_data in hourly_project_data:
        for key, _ in project_data:
            modified_headers.append(key)

    modified_headers = list(set(modified_headers))  # Remove duplicate headers

    table_data = []
    for project_data in hourly_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in modified_headers])

    print(tabulate(table_data, headers=modified_headers, tablefmt="grid"))

if __name__ == "__main__":
    p = sample_search_projects()
    save_projects_to_csv(p)
    print_projects_table(p)
    print_hourly_project_info_table(p)

Search results saved to CSV file: projects_search_results.csv
+----------+------------+---------------------------------------------------------------+----------+----------------+--------------------------------------------------------+---------------+-----------------+-----------------+-------------------+--------------------------+--------------------+------------------------+-----------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+------------------+------------------+---------------+-----------------------+----------------------+----------------------------------------+-------------------------------------------+-------------------------------------+------------+----------+------------+----------------------------+-----------------------+---------------------+------------------+----------------+------

In [31]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate

load_dotenv()

def extract_values(data, prefix=''):
    if isinstance(data, dict):
        result = []
        for key, value in data.items():
            result.extend(extract_values(value, prefix=f"{prefix}_{key}" if prefix else key))
        return result
    else:
        return [(prefix, data if data is not None else '')]

def flatten_project_data(project):
    flattened_project = []
    for key, value in project.items():
        flattened_project.extend(extract_values(value, prefix=key))
    return flattened_project

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=30
        )

        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found.")
        return

    csv_file_path = 'projects_search_results.csv'
    with open(csv_file_path, mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)

        modified_headers = []
        for key, _ in extract_values(projects[0]):
            modified_headers.append(key)

        writer.writerow(modified_headers)
        
        for project in projects:
            flattened_project = flatten_project_data(project)
            row_data = {key: value for key, value in flattened_project}
            writer.writerow([row_data.get(header, '') for header in modified_headers])

    print(f"Search results saved to CSV file: {csv_file_path}")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    modified_headers = []
    for key, _ in extract_values(projects[0]):
        modified_headers.append(key)

    modified_project_data = [flatten_project_data(project) for project in projects]

    table_data = []
    for project_data in modified_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in modified_headers])

    print(tabulate(table_data, headers=modified_headers, tablefmt="grid"))



if __name__ == "__main__":
    p = sample_search_projects()
    if p:
        save_projects_to_csv(p)
        print_projects_table(p)
        print_hourly_project_info_table(p)


Search results saved to CSV file: projects_search_results.csv
+----------+------------+---------------------------------------------------------------+----------+----------------+--------------------------------------------------------+---------------+-----------------+-----------------+-------------------+--------------------------+--------------------+------------------------+-----------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+------------------+------------------+---------------+-----------------------+----------------------+----------------------------------------+-------------------------------------------+-------------------------------------+------------+----------+------------+----------------------------+-----------------------+---------------------+------------------+----------------+------

In [32]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate
import json

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=100
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def extract_values(data, prefix=''):
    if isinstance(data, dict):
        result = []
        for key, value in data.items():
            result.extend(extract_values(value, prefix=f"{prefix}_{key}" if prefix else key))
        return result
    else:
        return [(prefix, data)]

def flatten_project_data(project):
    flattened_project = []
    for key, value in project.items():
        flattened_project.extend(extract_values(value, prefix=key))
    return flattened_project

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    modified_headers = []
    for key, _ in extract_values(projects[0]):
        modified_headers.append(key)

    modified_project_data = [flatten_project_data(project) for project in projects]

    table_data = []
    for project_data in modified_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in modified_headers])

    print(tabulate(table_data, headers=modified_headers, tablefmt="grid"))
p = sample_search_projects()
save_projects_to_csv(p)
print_projects_table(p)


Search results saved to CSV file: projects_search_results.csv
+----------+------------+-----------------------------------------------------------------------------+----------+----------------+-----------------------------------------------------------+---------------+-----------------+-----------------+-------------------+--------------------------+--------------------+------------------------+-----------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+------------------+------------------+---------------+-----------------------+----------------------+----------------------------------------+-------------------------------------------+-------------------------------------+------------+----------+------------+----------------------------+-----------------------+---------------------+------------------+------

In [33]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    query = 'Logo Design'
    
    try:
        response = search_projects(
            session,
            query=query,
            limit=100
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    except KeyboardInterrupt:
        print("Search interrupted by the user.")
        return None
    else:
        return projects

def extract_values(data, prefix=''):
    if isinstance(data, dict):
        result = []
        for key, value in data.items():
            result.extend(extract_values(value, prefix=f"{prefix}_{key}" if prefix else key))
        return result
    else:
        return [(prefix, data)]

def flatten_project_data(project):
    flattened_project = []
    for key, value in project.items():
        flattened_project.extend(extract_values(value, prefix=key))
    return flattened_project

def save_projects_to_csv(projects):
    if not projects:
        print("No projects found to save.")
        return

    with open('projects.csv', mode='w', newline='') as file:
        writer = csv.writer(file)
        writer.writerow(projects[0].keys())  # Write headers
        for project in projects:
            writer.writerow(project.values())
    print("Projects saved to CSV file.")

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    modified_headers = []
    for key, _ in extract_values(projects[0]):
        modified_headers.append(key)

    modified_project_data = [flatten_project_data(project) for project in projects]

    table_data = []
    for project_data in modified_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in modified_headers])

    print(tabulate(table_data, headers=modified_headers, tablefmt="grid"))

projects = sample_search_projects()
if projects:
    save_projects_to_csv(projects)
    print_projects_table(projects)


Projects saved to CSV file.
+----------+------------+-----------------------------------------------------------------------------+----------+----------------+-----------------------------------------------------------+---------------+-----------------+-----------------+-------------------+--------------------------+--------------------+------------------------+-----------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+------------------+------------------+---------------+-----------------------+----------------------+----------------------------------------+-------------------------------------------+-------------------------------------+------------+----------+------------+----------------------------+-----------------------+---------------------+------------------+----------------+---------------------+-

In [34]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate
import json

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=100  # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def extract_values(data, prefix=''):
    if isinstance(data, dict):
        result = []
        for key, value in data.items():
            result.extend(extract_values(value, prefix=f"{prefix}_{key}" if prefix else key))
        return result
    else:
        return [(prefix, data)]

def flatten_project_data(project):
    flattened_project = []
    for key, value in project.items():
        flattened_project.extend(extract_values(value, prefix=key))
    return flattened_project

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    modified_headers = []
    for key, _ in extract_values(projects[0]):
        modified_headers.append(key)

    modified_project_data = [flatten_project_data(project) for project in projects]

    table_data = []
    for project_data in modified_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in modified_headers])

    print(tabulate(table_data, headers=modified_headers, tablefmt="grid"))

p = sample_search_projects()
print_projects_table(p)


+----------+------------+------------------------------------------------------------------------------------------------+----------+----------------+--------------------------------------------------------------------+---------------+-----------------+-----------------+--------------------+--------------------------+--------------------+------------------------+-----------------------------------+---------------+--------+--------------+------------------------------------------------------------------------------------------------------+-----------+-------------+------------+--------+-------------+------------------+------------------+---------------+-----------------------+----------------------+-----------------------+------------+----------+------------+----------------------------+-----------------------+---------------------+------------------+----------------+---------------------+-------------------+----------------------+---------------------+-------------------+--------------

In [58]:
import os
import pandas as pd
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=10   # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def flatten_project_data(project, prefix=''):
    flattened_data = {}

    for key, value in project.items():
        if isinstance(value, dict):
            flattened_data.update(flatten_project_data(value, prefix=f"{prefix}_{key}"))
        else:
            flattened_data[f"{prefix}_{key}"] = value

    return flattened_data

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    flattened_projects = [flatten_project_data(project) for project in projects]
    df = pd.DataFrame(flattened_projects)

    print(df)

    # Save DataFrame to CSV file
    csv_filename = "projects.csv"
    df.to_csv(csv_filename, index=False)
    print(f"DataFrame saved to {csv_filename}")

projects = sample_search_projects()
print_projects_table(projects)


        _id  _owner_id                                             _title  \
0  37858136    4515755  Synology NAS Email Server Setup for Inbound an...   
1  37856686   30211151        Ubuntu Crytpitan Installation Expert Needed   
2  37858128   75002001              Clothing Print Company Website Design   
3  37858126   41886661                                  Anomaly detection   
4  37858125   29147477  I want to promote my family's exit from Gaza c...   
5  37857260   36291965                            Backdrop CMS Conversion   
6  37858116   75001957                    Electronics Product Photography   
7  37858117   72220287  Engaging Explainer and Product Demonstration V...   
8  37858109   75000990                  Dynamic Content Creator for Video   
9  37858106   75001930                 Creative Business Operations Video   

  _status     _sub_status                                           _seo_url  \
0  active            None                dns/Synology-NAS-Email-Server-S

In [1]:
import os
import pandas as pd
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=3   # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def flatten_project_data(project, prefix=''):
    flattened_data = {}

    for key, value in project.items():
        if isinstance(value, dict):
            flattened_data.update(flatten_project_data(value, prefix=f"{prefix}_{key}"))
        else:
            flattened_data[f"{prefix}_{key}"] = value

    return flattened_data

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    # Flatten projects
    flattened_projects = [flatten_project_data(project) for project in projects]

    # Add an empty proposal column
    for project in flattened_projects:
        project['proposal'] = ''

    # Create DataFrame
    df = pd.DataFrame(flattened_projects)

    # Print DataFrame
    print(df)

    # Save DataFrame to CSV file
    csv_filename = "projects.csv"
    df.to_csv(csv_filename, index=False)
    print(f"DataFrame saved to {csv_filename}")

# Sample search projects and print the table
projects = sample_search_projects()
print_projects_table(projects)


        _id  _owner_id                                      _title _status  \
0  37861845   75026734     AI-Generated Religious Education Videos  active   
1  37861014   13375096  Comprehensive Animation Movie Studio Setup  active   
2  37861013   70000227              Investment Research Consulting  active   

  _sub_status                                           _seo_url  \
0        None     animation/Generated-Religious-Education-Videos   
1        None     animation/Comprehensive-Animation-Studio-Setup   
2        None  financial-research/Investment-Research-Consulting   

   _currency_id _currency_code _currency_sign     _currency_name  ...  \
0             1            USD              $          US Dollar  ...   
1            11            INR              ₹       Indian Rupee  ...   
2             3            AUD              $  Australian Dollar  ...   

   _project_source _project_source_reference  _quality_details  \
0             None                      None           

In [49]:
import os
import pandas as pd
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException

load_dotenv()

def sample_search_projects():
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(session, query='', limit=10)
        projects = response.get('projects', [])
        return projects
    except ProjectsNotFoundException as e:
        print(f'Error: {e.message} (Code: {e.error_code})')
        return None

def flatten_project_data(project, prefix=''):
    flattened_project = {}
    sorted_keys = sorted(project.keys())

    for key in sorted_keys:
        value = project[key]
        if isinstance(value, dict):
            flattened_project.update(flatten_project_data(value, prefix=f"{prefix}_{key}"))
        else:
            flattened_project[f"{prefix}_{key}"] = value

    return flattened_project

def print_projects_table(projects, output_file='projects.csv'):
    if not projects:
        print("No projects found.")
        return

    modified_project_data = [flatten_project_data(project) for project in projects]
    df = pd.DataFrame(modified_project_data)

    # Format the DataFrame for better readability
    styled_df = (
        df.style
        .set_properties(**{'text-align': 'left'})
        .set_table_styles([
            {'selector': 'th', 'props': [('background-color', '#4CAF50'), ('color', 'white'), ('font-weight', 'bold')]},
            {'selector': 'tr:hover', 'props': [('background-color', '#f5f5f5')]},
            {'selector': '', 'props': [('border', '1px solid #ddd')]},
        ])
    )

    print(styled_df)
    df.to_csv(output_file, index=False)
    print(f"Projects data saved to '{output_file}'")

projects = sample_search_projects()
if projects:
    print_projects_table(projects)

Projects data saved to 'projects.csv'


In [37]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=15  # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def flatten_project_data(project, prefix=''):
    flattened_project = {}

    # Sort keys for consistent order
    sorted_keys = sorted(project.keys())

    for key in sorted_keys:
        value = project[key]
        if isinstance(value, dict):
            # Recursively flatten nested dictionaries
            flattened_subproject = flatten_project_data(value, prefix=f"{prefix}_{key}")
            flattened_project.update(flattened_subproject)
        else:
            flattened_project[f"{prefix}_{key}"] = value

    return flattened_project

def save_projects_to_csv(projects, filename):
    if not projects:
        print("No projects found.")
        return

    # Flatten the project data for CSV writing
    flattened_projects = [flatten_project_data(project) for project in projects]

    # Get all unique headers
    headers = set()
    for project_data in flattened_projects:
        headers.update(project_data.keys())

    # Write data to CSV file
    with open(filename, 'w', newline='') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=sorted(headers))
        writer.writeheader()

        for project_data in flattened_projects:
            writer.writerow(project_data)

    print(f"Projects data saved to {filename}")

p = sample_search_projects()
save_projects_to_csv(p, 'projects_data.csv')


Projects data saved to projects_data.csv


In [38]:
import os
import csv
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from freelancersdk.resources.projects import create_milestone_payment
from freelancersdk.resources.projects.types import MilestoneReason
from freelancersdk.exceptions import MilestoneNotCreatedException

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=15  # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def flatten_project_data(project, prefix=''):
    flattened_project = {}

    # Sort keys for consistent order
    sorted_keys = sorted(project.keys())

    for key in sorted_keys:
        value = project[key]
        if isinstance(value, dict):
            # Recursively flatten nested dictionaries
            flattened_subproject = flatten_project_data(value, prefix=f"{prefix}_{key}")
            flattened_project.update(flattened_subproject)
        else:
            flattened_project[f"{prefix}_{key}"] = value

    return flattened_project

def save_projects_to_csv(projects, filename):
    if not projects:
        print("No projects found.")
        return

    # Flatten the project data for CSV writing
    flattened_projects = [flatten_project_data(project) for project in projects]

    # Get all unique headers
    headers = set()
    for project_data in flattened_projects:
        headers.update(project_data.keys())

    # Write data to CSV file
    with open(filename, 'w', newline='') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=sorted(headers))
        writer.writeheader()

        for project_data in flattened_projects:
            writer.writerow(project_data)

    print(f"Projects data saved to {filename}")

def sample_create_milestone_payment():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')
    bidder_id = os.environ.get('BIDDER_ID')

    if not all([url, oauth_token, project_id, bidder_id]):
        print("Missing required environment variables.")
        return None

    try:
        project_id = int(project_id)
        bidder_id = int(bidder_id)
    except (TypeError, ValueError):
        print("Invalid project_id or bidder_id.")
        return None

    session = Session(oauth_token=oauth_token, url=url)
    milestone_data = {
        'project_id': project_id,
        'bidder_id': bidder_id,
        'amount': 10,
        'reason': MilestoneReason.PARTIAL_PAYMENT.value,
        'description': 'This is a milestone',
    }

    try:
        m = create_milestone_payment(session, **milestone_data)
    except MilestoneNotCreatedException as e:
        print(('Error message: %s' % e.message))
        print(('Server response: %s' % e.error_code))
        return None
    else:
        return m

# Main code
if __name__ == "__main__":
    # Fetch and save projects data
    projects = sample_search_projects()
    save_projects_to_csv(projects, 'projects_data.csv')

    # Create milestone payment
    milestone = sample_create_milestone_payment()
    if milestone:
        print(("Milestone created: %s" % milestone))


Projects data saved to projects_data.csv
Missing required environment variables.


In [39]:
import os
import csv
import json
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    search_projects, get_projects, get_project_by_id, place_project_bid
)
from freelancersdk.resources.projects.exceptions import (
    ProjectsNotFoundException, MilestoneNotCreatedException, BidNotPlacedException
)
from freelancersdk.resources.projects import create_milestone_payment
from freelancersdk.resources.projects.types import MilestoneReason
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.users import get_self_user_id

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=10  # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def flatten_project_data(project, prefix=''):
    flattened_project = {}

    # Sort keys for consistent order
    sorted_keys = sorted(project.keys())

    for key in sorted_keys:
        value = project[key]
        if isinstance(value, dict):
            # Recursively flatten nested dictionaries
            flattened_subproject = flatten_project_data(value, prefix=f"{prefix}{'' if prefix == '' else '_'}{key}")
            flattened_project.update(flattened_subproject)
        else:
            flattened_project[f"{prefix}{'' if prefix == '' else '_'}{key}"] = value

    return flattened_project


def save_projects_to_csv(projects, filename):
    if not projects:
        print("No projects found.")
        return

    # Flatten the project data for CSV writing
    flattened_projects = [flatten_project_data(project) for project in projects]

    # Get all unique headers
    headers = set()
    for project_data in flattened_projects:
        headers.update(project_data.keys())

    # Write data to CSV file
    with open(filename, 'w', newline='') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=sorted(headers))
        writer.writeheader()

        for project_data in flattened_projects:
            writer.writerow(project_data)

    print(f"Projects data saved to {filename}")

def sample_create_milestone_payment(project_id, bidder_id):
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')

    if not all([url, oauth_token, project_id, bidder_id]):
        print("Missing required environment variables.")
        return None

    try:
        project_id = int(project_id)
        bidder_id = int(bidder_id)
    except (TypeError, ValueError):
        print("Invalid project_id or bidder_id.")
        return None

    session = Session(oauth_token=oauth_token, url=url)
    milestone_data = {
        'project_id': project_id,
        'bidder_id': bidder_id,
        'amount': 10,
        'reason': MilestoneReason.PARTIAL_PAYMENT.value,
        'description': 'This is a milestone',
    }

    try:
        m = create_milestone_payment(session, **milestone_data)
    except MilestoneNotCreatedException as e:
        print(('Error message: %s' % e.message))
        print(('Server response: %s' % e.error_code))
        return None
    else:
        return m

def sample_get_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    query = create_get_projects_object(
        project_ids=[
            201,
            202,
            203,
        ],
        project_details=create_get_projects_project_details_object(
            full_description=True,
            jobs=True,
            qualifications=True,
        ),
        user_details=create_get_projects_user_details_object(
            basic=True,
            profile_description=True,
            reputation=True,
        ),
    )

    try:
        p = get_projects(session, query)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_get_project_by_id():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token, url=url)

    project_id = 15389177
    project_details = create_get_projects_project_details_object(
        full_description=True
    )
    user_details = create_get_projects_user_details_object(
        basic=True
    )

    try:
        p = get_project_by_id(session, project_id, project_details, user_details)
    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return p

def sample_place_project_bid():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    project_id = os.environ.get('PROJECT_ID')

    session = Session(oauth_token=oauth_token, url=url)

    try:
        my_user_id = get_self_user_id(session)
    except:
        # User ID not retrieved. Handle the error here, e.g., print an error message.
        return None

    bid_data = {
        'project_id': int(project_id),
        'bidder_id': my_user_id,
        'amount': 10,
        'period': 2,
        'milestone_percentage': 100,
        'description': 'This is my bid',
    }

    try:
        return place_project_bid(session, **bid_data)
    except BidNotPlacedException as e:
        print(('Error message: %s' % e.message))
        print(('Error code: %s' % e.error_code))
        return None

# Main code
if __name__ == "__main__":
    # Fetch and save projects data
    projects = sample_search_projects()
    save_projects_to_csv(projects, 'projects_data.csv')

    # Create milestone payment
    project_id = os.environ.get('PROJECT_ID')
    bidder_id = os.environ.get('BIDDER_ID')
    milestone = sample_create_milestone_payment(project_id, bidder_id)
    if milestone:
        print(("Milestone created: %s" % milestone))

    # Fetch and print multiple projects
    print('Getting multiple projects...')
    p = sample_get_projects()
    if p:
        print('Found projects: {}'.format(json.dumps(p)))

    # Fetch and print a single project by ID
    print('Getting a single project by ID...')
    p = sample_get_project_by_id()
    if p:
        print('Found a single project: {}'.format(json.dumps(p)))

    # Place a project bid
    b = sample_place_project_bid()
    if b:
        print(("Bid placed: %s" % b))


Projects data saved to projects_data.csv
Missing required environment variables.
Getting multiple projects...
Found projects: {"projects": [{"id": 201, "owner_id": 2684, "title": "Boot to application", "status": "closed", "sub_status": "closed_expired", "seo_url": "Boot-application-project", "currency": {"id": 1, "code": "USD", "sign": "$", "name": "US Dollar", "exchange_rate": 1.0, "country": "US", "is_external": false, "is_escrowcom_supported": true}, "description": "To provide a boot sequence for ms windows such that from switching on\r\nthe mains the computer loads an application and displays files on the monitor without any further interaction after switching on. i.e no passwords, start menu-application, etc.  I envisage boot - load browser - display html files (starting with home page) It could be some other application, but browser/html files seems the most common and, because these files have to be uploaded would probably be easier. ", "jobs": [], "submitdate": 1077810438, "pre

In [40]:
import os
import csv
import json
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import (
    search_projects, get_projects, get_project_by_id, place_project_bid
)
from freelancersdk.resources.projects.exceptions import (
    ProjectsNotFoundException, MilestoneNotCreatedException, BidNotPlacedException
)
from freelancersdk.resources.projects import create_milestone_payment
from freelancersdk.resources.projects.types import MilestoneReason
from freelancersdk.resources.projects.helpers import (
    create_get_projects_object, create_get_projects_project_details_object,
    create_get_projects_user_details_object
)
from freelancersdk.resources.users import get_self_user_id

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=20  # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        return {'error': 'Projects not found'}
    else:
        return {'projects': projects}

# Define other utility functions (fetch_single_project, place_bid, create_milestone) similarly

# Fetch and save projects data
projects_data = sample_search_projects()

# Display projects data
print(projects_data)


{'projects': [{'id': 37857887, 'owner_id': 66385017, 'title': 'Holistic Digital Marketing & SEO Enhancement', 'status': 'active', 'sub_status': None, 'seo_url': 'internet-marketing/Holistic-Digital-Marketing-SEO', 'currency': {'id': 11, 'code': 'INR', 'sign': '₹', 'name': 'Indian Rupee', 'exchange_rate': 0.012084, 'country': 'IN', 'is_external': False, 'is_escrowcom_supported': False}, 'description': None, 'jobs': None, 'submitdate': 1709971019, 'preview_description': "I'm seeking a seasoned digital marketing expert who can elevate the online presence of my business. ", 'deleted': False, 'nonpublic': False, 'hidebids': False, 'type': 'hourly', 'bidperiod': 7, 'budget': {'minimum': 750.0, 'maximum': 1250.0, 'name': None, 'project_type': None, 'currency_id': None}, 'hourly_project_info': {'commitment': {'hours': 40, 'interval': 'week'}, 'duration_enum': 'unspecified'}, 'featured': False, 'urgent': False, 'assisted': None, 'active_prepaid_milestone': None, 'bid_stats': {'bid_count': 2, 'b

In [41]:
import os
from dotenv import load_dotenv
from freelancersdk.session import Session
from freelancersdk.resources.projects.projects import search_projects
from freelancersdk.resources.projects.exceptions import ProjectsNotFoundException
from tabulate import tabulate

load_dotenv()

def sample_search_projects():
    url = os.environ.get('FLN_URL')
    oauth_token = os.environ.get('FLN_OAUTH_TOKEN')
    session = Session(oauth_token=oauth_token)

    try:
        response = search_projects(
            session,
            query='',  # Empty query to retrieve all projects
            limit=10  # You can adjust the limit as needed
        )

        # Extract the list of projects
        projects = response.get('projects', [])

    except ProjectsNotFoundException as e:
        print('Error message: {}'.format(e.message))
        print('Server response: {}'.format(e.error_code))
        return None
    else:
        return projects

def flatten_project_data(project, prefix=''):
    flattened_project = []

    # Sort keys for consistent order
    sorted_keys = sorted(project.keys())

    for key in sorted_keys:
        value = project[key]
        if isinstance(value, dict):
            flattened_project.extend(flatten_project_data(value, prefix=f"{prefix}_{key}"))
        else:
            flattened_project.append((f"{prefix}_{key}", value))

    return flattened_project

def print_projects_table(projects):
    if not projects:
        print("No projects found.")
        return

    modified_project_data = [flatten_project_data(project) for project in projects]

    headers = set()
    for project_data in modified_project_data:
        headers.update([key for key, _ in project_data])

    table_data = []
    for project_data in modified_project_data:
        row_data = {key: value for key, value in project_data}
        table_data.append([row_data.get(header, '') for header in sorted(headers)])  # Sort headers here

    print(tabulate(table_data, headers=sorted(headers), tablefmt="grid"))

    # Proposal Box and Project Summary
    print("\nProposal Box:")
    for project in projects:
        print(f"Project ID: {project.get('_id')}")
        print(f"Title: {project.get('_title')}")
        print(f"Description: {project.get('_description')}")
        print(f"Bid Count: {project.get('_bid_stats_bid_count')}")

        # Prompt to generate proposal
        print("\nGenerate Proposal?")
        # Add your logic here to prompt the user to generate a proposal

p = sample_search_projects()
print_projects_table(p)


+-----------------------------+-------------+----------------+----------------------+------------------------+--------------+-----------------+-----------------------+-------------------+-------------------+----------------+------------------------+--------------------+----------------------+------------------------+------------------+---------------------+---------------------------+----------------+------------------------------------+-------------------------+-------------------+------------------+------------+---------------------+----------------+----------------+-------------------+---------------------------------------+-------------------------------+----------------+--------------+---------------------+-------------+----------+-----------------------+----------------------------+--------------+-------------+-----------+-----------------------+------------------------+-----------------------------------------+--------------------------------------------+------------------------

In [45]:
from freelancersdk.session import Session

# Replace with your freelancer access token
oauth_token = "YOUR_OAUTH_TOKEN"

session = Session(oauth_token=oauth_token)

# Replace with your project and bid details
project_id = 37869764
bidder_id = 98765
description = "This is my proposal"
amount = 100
period = 5
milestone_percentage = 50

try:
    bid = place_project_bid(session, project_id, bidder_id, description, amount, period, milestone_percentage)
    print("Bid placed! Details:")
    # Access bid details using bid object attributes (assuming a Bid class)
    print(f"  Project ID: {bid.project_id}")
    print(f"  Amount: {bid.amount}")
    # ... (print other relevant attributes)
except BidNotPlacedException as e:
    print(f"Error placing bid: {e}")  # Print the entire exception object


Error placing bid: You must be logged in to perform this request
